In [2]:
%load_ext autoreload
%autoreload 2

In [3]:
import os
import sys
import pandas as pd
import numpy as np
module_path = os.path.abspath(os.path.join('..','src','event_reader'))
sys.path.append(module_path)

from event_history_v3 import get_event_logs_threads
from util import get_web3, read_abi
import plotly.express as px

In [4]:
token_address = "0x6B175474E89094C44Da98b954EedeAC495271d0F"

In [5]:
w3 = get_web3()
name_tag = 'USDC_ETH'
pair_address = w3.toChecksumAddress("0xb4e16d0168e52d35cacd2c6185b44281ec28c9dc")
contract = w3.eth.contract(address=pair_address, abi = read_abi('pair',pair_address))
token_0 = contract.functions.token0().call()
token_1 = contract.functions.token1().call()

token_abi = read_abi('token', token_address)
token_cont_base = w3.eth.contract(abi=token_abi)

tok_0_cont = token_cont_base(address=token_0)
tok_0_dec = tok_0_cont.functions.decimals().call()

tok_1_cont = token_cont_base(address=token_1)
tok_1_dec = tok_1_cont.functions.decimals().call()

tok_0_dec, tok_1_dec

(6, 18)

In [6]:
stop = 14785568
start = 0
step = 1000

In [7]:
sync_logs = get_event_logs_threads(w3, pair_address, ['Sync'], start, stop, step)

INFO:root:Found total 3485027 events
INFO:root:parsing events...


In [55]:
sync_data = {'tx_hash':[],'block':[],'log_index':[],'res0':[],'res1':[]}
for log in sync_logs:
    tx = log['transactionHash'].hex()
    block = log['blockNumber']
    log_index = log['logIndex']
    res_0 = log['args']['reserve0']
    res_1 = log['args']['reserve1']
                  
    sync_data['tx_hash'].append(tx)
    sync_data['block'].append(block)
    sync_data['log_index'].append(log_index)
    sync_data['res0'].append(res_0)
    sync_data['res1'].append(res_1)
                  
df_sync = pd.DataFrame(sync_data)                 

In [9]:
fill_logs = get_event_logs_threads(w3, pair_address, ['Mint', 'Burn'], start, stop, step)

INFO:root:Found total 57928 events
INFO:root:parsing events...


In [54]:
fill_dict = {'tx_hash':[],'block':[],'log_index':[],'delta0':[],'delta1':[]}
for log in fill_logs:
    tx = log['transactionHash'].hex()
    block = log['blockNumber']
    log_index = log['logIndex']
    if log['event']=='Mint':
        #delta_0 = log['args']['amount0In'] - log['args']['amount0Out']
        #delta_1 = log['args']['amount1In'] - log['args']['amount1Out']
        delta_0 = log['args']['amount0']
        delta_1 = log['args']['amount1']
    elif log['event'] == 'Burn':
        delta_0 = -log['args']['amount0']
        delta_1 = -log['args']['amount1']
    fill_dict['tx_hash'].append(tx)
    fill_dict['block'].append(block)
    fill_dict['log_index'].append(log_index)
    fill_dict['delta0'].append(delta_0)
    fill_dict['delta1'].append(delta_1)
df_fill = pd.DataFrame(fill_dict)

In [56]:
df_fill_adj = df_fill.copy()
df_fill_adj['log_index'] = df_fill_adj['log_index'] - 1

In [57]:
df = pd.merge(df_sync, df_fill_adj, on=['tx_hash', 'block', 'log_index'], how='left').fillna(0)
df = df.sort_values(by=['block','log_index']).reset_index(drop=True)
#df[['res0','res1','delta0','delta1']] = df[['res0','res1','delta0','delta1']].astype('Decimal')


df['prev0'] = (df['res0'] - df['delta0']).shift(-1)
df['prev1'] = (df['res1'] - df['delta1']).shift(-1)
df.dropna(inplace=True)
df['sqrt_k1'] = (np.sqrt(df['res0'].astype('float') * df['res1'].astype('float')))
df['sqrt_k2'] = (np.sqrt(df['prev0'].astype('float') * df['prev1'].astype('float')))
df['ret'] = 1 - (df['sqrt_k1']/df['sqrt_k2'])
df

tx_hash     block  \
0        0x2ef96febd1777e0403768e45e46dbd677f21079ba5f8...  10008555   
1        0x932cb88306450d481a0e43365a3ed832625b68f036e9...  10008566   
2        0x697b7aaca56a80a8d3a2f560ed7f1ecb97c22b2edd6e...  10008585   
3        0x43b6bfd06dde0814fe9c1b63ce98ec4c67c72d96169d...  10013764   
4        0x735cf98e86a5df67b6a837ae50de1d7a589d9f6baaf0...  10014418   
...                                                    ...       ...   
3485021  0x672dd5dfb601291ebeff7815aeb50c146a37d48c152c...  14785552   
3485022  0x99053faaf3c34e59d621b3e8cfdaa049fdb4779a7f70...  14785555   
3485023  0x48b5b1e94b3ac757e1906bb3e0ce584e7bf58ac1c3fd...  14785562   
3485024  0xd2f65de0693b4fd35e7713166666c37cc0ebe0a91bca...  14785563   
3485025  0x9d2ddbf01c648b673f88a043d9363fc6227a5bebd287...  14785564   

         log_index            res0                     res1     delta0  \
0               23         1000000         4854368932000000  1000000.0   
1                3          999000         4859242781709289        0.0   
2                3          989000         4908523513507407        0.0   
3               75          988000         4913506603986849        0.0   
4               36          988689         4910094205790933        0.0   
...            ...             ...                      ...        ...   
3485021         48  98903937124718  49146784782747207777948        0.0   
3485022         67  98903210278688  49147147052427237544918        0.0   
3485023        136  98903100894980  49147201571177237544918        0.0   
3485024         23  98901897100808  49147801571177237544918        0.0   
3485025        409  98901696471303  49147901571177237544918        0.0   

                   delta1         prev0                    prev1  \
0        4854368932000000  9.990000e+05         4859242781709289   
1                       0  9.890000e+05         4908523513507407   
2                       0  9.880000e+05         4913506603986849   
3                       0  9.886890e+05         4910094205790933   
4                       0  9.886890e+05         4910094205790933   
...                   ...           ...                      ...   
3485021                 0  9.890321e+13  49147147052427237544918   
3485022                 0  9.890310e+13  49147201571177237544918   
3485023                 0  9.890190e+13  49147801571177237544918   
3485024                 0  9.890170e+13  49147901571177237544918   
3485025                 0  9.889232e+13  49152577063257237544918   

              sqrt_k1       sqrt_k2           ret  
0        6.967330e+10  6.967341e+10  1.504510e-06  
1        6.967341e+10  6.967446e+10  1.505986e-05  
2        6.967446e+10  6.967456e+10  1.521244e-06  
3        6.967456e+10  6.967464e+10  1.195320e-06  
4        6.967464e+10  6.967464e+10  0.000000e+00  
...               ...           ...           ...  
3485021  2.204725e+18  2.204725e+18  1.105669e-08  
3485022  2.204725e+18  2.204725e+18  1.663946e-09  
3485023  2.204725e+18  2.204725e+18  1.831211e-08  
3485024  2.204725e+18  2.204725e+18  3.052016e-09  
3485025  2.204725e+18  2.204725e+18  1.426830e-07  

[3485026 rows x 12 columns]

In [59]:
# Group by removing last 2 digits
# 100 blocks, 15s per block = 1500s = 25min
df_25min = df.copy()

df_25min['grouping'] = df_25min['block'].astype('str').str[:-2]
data_25 = df_25min.groupby(by='grouping').sum().reset_index()
px.scatter(data_25, x='grouping', y='ret')

In [60]:
# 3 digits
# 1k blocks, 4.1h
df_4h = df.copy()

df_4h['grouping'] = df_4h['block'].astype('str').str[:-3]
data_4h = df_4h.groupby(by='grouping').sum().reset_index()
px.scatter(data_4h, x='grouping', y='ret')

In [61]:
# 4 digits
# 10k blocks, 1.7d
df_1d = df.copy()

df_1d['grouping'] = df_1d['block'].astype('str').str[:-4]
data_1d = df_1d.groupby(by='grouping').sum().reset_index()
px.scatter(data_1d, x='grouping', y='ret')

In [85]:
price_df = df.copy()
price_df['price'] = (price_df['res0']/pow(10,6)) / (price_df['res1']/pow(10,18)).astype(float)
price_df['grouping'] = price_df['block'].astype('str').str[:-4]

ret_data = price_df.groupby(by='grouping').sum().reset_index()['ret']
ret_data = ret_data * (365/(10000*15/60/60/24))

price_data = price_df.groupby(by='grouping').mean().reset_index()['price']

In [134]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Create figure with secondary y-axis
fig = make_subplots(specs=[[{"secondary_y": True}]])

blue = "Returns"
red = "volatility"

# Add traces
fig.add_trace(
    go.Scatter(x=data_df.index, y=data_df['ret'], name=blue),
    secondary_y=False,
)

fig.add_trace(
    go.Scatter(x=data_df.index, y=data_df['volatility'], name=red),
    secondary_y=True,
)

# Add figure title
fig.update_layout(
    title_text="Double Y Axis Example"
)

# Set x-axis title
fig.update_xaxes(title_text="Thousand blocks (≈1.7 days)")

# Set y-axes titles
fig.update_yaxes(title_text=blue, secondary_y=False)
fig.update_yaxes(title_text=red, secondary_y=True)

fig.show()

In [133]:
data_df = pd.concat([ret_data,price_data],axis=1)
data_df['price_move'] = data_df['price'].pct_change()
data_df['price_move_abs'] = abs(data_df['price_move'])
data_df['price_move_abs_avg'] = data_df['price_move_abs'].rolling(10).mean()
data_df['volatility'] = data_df['price_move'].rolling(3).std()
data_df = data_df.dropna()

In [126]:
data_df['price_move_abs'].rolling(10).mean()

1           NaN
2           NaN
3           NaN
4           NaN
5      0.233631
         ...   
473    0.038072
474    0.053189
475    0.066229
476    0.057642
477    0.053636
Name: price_move_abs, Length: 477, dtype: float64